Ссылки на служебные папки

In [4]:
import os.path

files_path = os.path.join('..', '..', 'files')
checkpoints_path = os.path.join(files_path, 'checkpoints')
models_path = os.path.join(files_path, 'models')

images_data_matrix_path = os.path.join(checkpoints_path, "images_data_matrix.pkl")
images_data_path = os.path.join(checkpoints_path, "images_data.pkl")
categories_data_path = os.path.join(checkpoints_path, "categories_data.pkl")

svm_model_path = os.path.join(models_path, 'svm_model.pkl')

Инициализация клиента Clickhouse.
Данные для входа запрашиваются отдельно.

Все выгруженные данные находятся в контрольных точках. Но их мало, тк объем данных в оригинальном виде очень большой.

In [ ]:
from src.databases import dwh

clickhouse_client = dwh.def_client()

Создание репозитория для получения информации из БД

In [ ]:
from src.data_access_layer.factories.sql_data_service_factory import DataServiceFactory

train_data_service = DataServiceFactory.get_train_data_service(clickhouse_client)

Получение всех имен картинок

In [ ]:
images = train_data_service.get_images_names()

Количество и список картинок

In [ ]:
print("Общее количество картинок:", len(images))

In [ ]:
print(*images, sep='\n')

Беру срез в 500 картинок. Чтобы пока использовать для тестового варианта.

In [ ]:
images500 = images[:500]

Получение матриц картинок

In [ ]:
images_data = []
image_data = {}

for image in images500:
    image_data['name'] = image
    image_data['data'] = train_data_service.get_images_data_by_image_name(image)
    images_data.append(image_data)

images_data

In [ ]:
import matplotlib.pyplot as plt

plt.imshow(images_data[0]['data'])

Контрольная точка. Сохранено 500 картинок

In [ ]:
import pickle

pickle.dump(images_data, open(images_data_matrix_path, 'wb'))
del images_data

Вытаскивание картинок на случай перезапуска

In [ ]:
import pickle

images_data = pickle.load(open(images_data_matrix_path, 'rb'))
images_data

In [ ]:
import matplotlib.pyplot as plt

plt.imshow(images_data[0]['data'])

In [ ]:
def extract_image_objects(image_data, train_service=train_data_service):
    image_name = image_data['name']
    return train_service.GetImagesObjectsByImageName(image_name)

In [ ]:
for image_data in images_data:
    image_data['objects'] = extract_image_objects(image_data)

images_data

Контрольная точка. Сохранено 500 картинок c их объектами

In [ ]:
import pickle

pickle.dump(images_data, open(images_data_path, 'wb'))
del images_data

Вытаскивание картинок на случай перезапуска

In [ ]:
import pickle

images_data = pickle.load(open(images_data_path, 'rb'))
images_data

In [ ]:
type(images_data[0]['data'][0])

Создание картинок по категориям

In [ ]:
def extract_crop(image, object_data):
    x1, y1 = int(object_data['box2d_x1']), int(object_data['box2d_y1'])
    x2, y2 = int(object_data['box2d_x2']), int(object_data['box2d_y2'])

    return image[y1:y2, x1:x2]

In [ ]:
img_categories = []

for image_data in images_data:
    img_objects = image_data['objects']

    for img_object in img_objects:
        img_category = {'category': img_object['category'], 'image': extract_crop(image_data['data'], img_object)}
        img_categories.append(img_category)

img_categories

In [ ]:
from matplotlib import pyplot as plt

plt.imshow(img_categories[0]['image'])

Контрольная точка сохранения категорий с их картинками

In [ ]:
import pickle

pickle.dump(img_categories, open(categories_data_path, 'wb'))
del img_categories
del images_data

In [ ]:
import pickle

img_categories = pickle.load(open(categories_data_path, 'rb'))

SIFT

Извлечение признаков (матрицы каналов картинки)

In [82]:
images = [x['image'] for x in img_categories]
images

[array([[[ 28,  27,  23],
         [ 32,  31,  27],
         [ 33,  32,  28],
         [ 31,  30,  26],
         [ 27,  26,  22],
         [ 25,  24,  20],
         [ 20,  19,  15],
         [ 22,  21,  17],
         [ 23,  22,  18],
         [ 20,  19,  15],
         [ 15,  14,  10],
         [ 12,  11,   7],
         [ 12,  11,   7],
         [ 14,  13,   9],
         [ 10,   9,   5],
         [ 11,  10,   6],
         [ 12,  11,   7]],
 
        [[ 28,  27,  23],
         [ 30,  29,  25],
         [ 30,  29,  25],
         [ 30,  29,  25],
         [ 29,  28,  24],
         [ 27,  26,  22],
         [ 23,  22,  18],
         [ 23,  22,  18],
         [ 22,  21,  17],
         [ 18,  17,  13],
         [ 14,  13,   9],
         [ 12,  11,   7],
         [ 12,  11,   7],
         [ 14,  13,   9],
         [  6,   5,   1],
         [ 12,  11,   7],
         [ 14,  13,   9]],
 
        [[ 30,  29,  25],
         [ 31,  30,  26],
         [ 32,  31,  27],
         [ 35,  34,  30],
      

Получение целевых значений

In [85]:
y = [x['category'] for x in img_categories]
y

['traffic sign',
 'traffic sign',
 'traffic light',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'traffic sign',
 'traffic sign',
 'traffic light',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'traffic sign',
 'traffic sign',
 'traffic light',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'traffic sign',
 'traffic sign',
 'traffic light',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'traffic sign',
 'traffic sign',
 'traffic light',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'car',
 'traffic sign',
 't

In [ ]:
len(images)

Список найденных категорий среди 500 картинок

In [86]:
set(y)

{'car', 'traffic light', 'traffic sign'}

Расчет дескрипторов по алгоритму SIFT для использования их в качестве признаков для обучения модели

In [83]:
from src.features_extraction_algorithms.sift_algorithm import extract_sift_descriptors

descriptors = extract_sift_descriptors(images)
descriptors

[array([[ 33.,   0.,   0.,   0.,   0.,   0.,   0.,  17., 155.,   0.,   0.,
           0.,  18.,  35.,  29., 138.,  18.,   0.,   0.,   0., 155., 155.,
          26.,  24.,   0.,   0.,   0.,   0.,  12.,   7.,   0.,   0.,  47.,
           1.,   0.,   0.,   0.,   0.,   0.,  14., 155.,  27.,   5.,   6.,
          47.,  11.,   1.,  67.,  46.,   7.,   5.,  22., 155.,  57.,   1.,
          12.,   0.,   0.,   0.,   1.,  32.,   4.,   0.,   0.,  21.,   8.,
           0.,   0.,   0.,   0.,   0.,   1., 155., 155.,  47.,  26.,  12.,
           0.,   0.,   4.,  13.,  33.,  49., 138., 155.,   6.,   0.,   0.,
           0.,   0.,   0.,   7.,  19.,   1.,   0.,   0.,   1.,   1.,   0.,
           0.,   0.,   0.,   0.,   0.,   4.,  15.,   4.,   2.,   0.,   0.,
           0.,   0.,   0.,   3.,   5.,  10.,   5.,   0.,   0.,   0.,   0.,
           0.,   0.,   1.,   1.,   0.,   0.,   0.],
        [  1.,   0.,   0.,   0.,   0.,   0.,   0.,   1.,   5.,   0.,   0.,
           0.,   0.,   3.,   5.,  11.,   0.,   0

Очистка от нулевых значений

In [76]:
all_descriptors = []
for descriptor in descriptors:
    if descriptor is not None:
        for des in descriptor:
            all_descriptors.append(des)

all_descriptors

[array([ 33.,   0.,   0.,   0.,   0.,   0.,   0.,  17., 155.,   0.,   0.,
          0.,  18.,  35.,  29., 138.,  18.,   0.,   0.,   0., 155., 155.,
         26.,  24.,   0.,   0.,   0.,   0.,  12.,   7.,   0.,   0.,  47.,
          1.,   0.,   0.,   0.,   0.,   0.,  14., 155.,  27.,   5.,   6.,
         47.,  11.,   1.,  67.,  46.,   7.,   5.,  22., 155.,  57.,   1.,
         12.,   0.,   0.,   0.,   1.,  32.,   4.,   0.,   0.,  21.,   8.,
          0.,   0.,   0.,   0.,   0.,   1., 155., 155.,  47.,  26.,  12.,
          0.,   0.,   4.,  13.,  33.,  49., 138., 155.,   6.,   0.,   0.,
          0.,   0.,   0.,   7.,  19.,   1.,   0.,   0.,   1.,   1.,   0.,
          0.,   0.,   0.,   0.,   0.,   4.,  15.,   4.,   2.,   0.,   0.,
          0.,   0.,   0.,   3.,   5.,  10.,   5.,   0.,   0.,   0.,   0.,
          0.,   0.,   1.,   1.,   0.,   0.,   0.], dtype=float32),
 array([  1.,   0.,   0.,   0.,   0.,   0.,   0.,   1.,   5.,   0.,   0.,
          0.,   0.,   3.,   5.,  11.,   0.,  

Получение модели на основе алгоритма k-средних

In [84]:
from src.features_extraction_algorithms.sift_algorithm import k_mean_bow

num_cluster = 60
bow = k_mean_bow(all_descriptors, num_cluster)

In [87]:
from src.features_extraction_algorithms.sift_algorithm import create_features_bow
from sklearn.model_selection import train_test_split

X_features = create_features_bow(descriptors, bow, num_cluster)

X_train, X_test, y_train, y_test = train_test_split(X_features, y, test_size=0.2, random_state=42)

In [99]:
from sklearn.svm import SVC

svm_model = SVC(C=10, random_state=42)
svm_model.fit(X_train, y_train)

SVC(C=10, random_state=42)

In [100]:
from sklearn.metrics import f1_score

y_pred = svm_model.predict(X_test)

print("f1 micro score on testing values: ", f1_score(y_test, y_pred, average='micro'))

f1 micro score on testing values:  0.9047619047619048


Результат выше неверный, тк модель недообучилась.

In [95]:
y_pred

array(['car', 'car', 'car', ..., 'car', 'car', 'car'], dtype='<U13')

In [102]:
import pickle

pickle.dump(svm_model, open(svm_model_path, 'wb'))